In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.


In [3]:
self.uid2uindex

{'u00': 4, 'u20': 2, 'u30': 4, 'u31': 4, 'u32': 7, 'u60': 8}

In [4]:
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
0       175      i0        1        동        남   571545870_02  571542797_02   
1       175      i0        2        서        동   571510153_02  571545870_01   
2       175      i0        3        남        서  -571542797_02  571510153_01   
3       175      i0        4        북        남  -571500487_01  571542797_02   
4       175      i0        5        서        북   571510153_02  571500487_01   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left

In [9]:
self.uid2uindex

{'u00': 4, 'u20': 2, 'u30': 4, 'u31': 4, 'u32': 7, 'u60': 8}

In [30]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 유턴노드를 제외한 모든 노드 (우회전, 삼지교차로직진 : g, 그외 : r)
for node_id in sorted(set(self.node_ids) - set(self.u_turn_ids)):
    node = self.net.getNode(node_id)
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns: # i번째 connection : ci
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # 합류지점이 다르면서 상충되는 cj가 존재하면 r, 그외에는 g
        for j, cj in conns: # j번째 connection : cj
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 유턴노드 (유턴x : G, 유턴 : G)
for node_id in self.u_turn_ids:
    node = self.net.getNode(node_id)
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        state.append('G')
    self.node2init[node_id] = state

# 신호가 부여되어 있는 경우에는 r을 부여 (우회전 : g, 그외 : r / 유턴x : G, 유턴 : r)
for _, row in self.match6.dropna(subset=['inc_edge_id', 'out_edge_id']).iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    inc_edge = self.net.getEdge(inc_edge_id)
    out_edge = self.net.getEdge(out_edge_id)
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            self.node2init[node_id][index] = 'r'
for node_id in self.node2init:
    print(node_id, ''.join(self.node2init[node_id]))

c30 rrrrrr
i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i7 rrrggrr
i8 grrrrrrrgrrrgrrr
i9 rrrr
u00 GGGGrGGGG
u20 GGrGGG
u30 GGGGrGGG
u31 GGGGrGGG
u32 GGGGGGGr
u60 GGGGGGGGr


In [10]:
import copy
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성
self.initialize_state() # 2-2 신호 초기화
display(self.matching[self.matching.node_id=='i2'])
# matching에 신호 배정
for i, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = self.net.getEdge(row.inc_edge_id)
    out_edge = self.net.getEdge(row.out_edge_id)
    state = copy.deepcopy(self.node2init[node_id])
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            state[index] = 'G'
    self.matching.at[i, 'state'] = ''.join(state)

display(self.matching[self.matching.node_id=='i2'])

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type  
32      left  
33  straight  
34      left  
35  straight  
36  straight  
37  straight  
38      left  
39  straight  
40      left  
41  straight  
42      left  
43  straight  
44  straight  
45  straight  
46      left  
47  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type    state  
32      left  rrggrrr  
33  straight  rrgGrrr  
34      left  rrggrrr  
35  straight  GGggrrr  
36  straight  rrggGGG  
37  straight  rrggrrr  
38      left  rrggrrr  
39  straight  rrggGGG  
40      left  rrggrrr  
41  straight  rrgGrrr  
42      left  rrggrrr  
43  straight  GGggrrr  
44  straight  rrggGGG  
45  straight  rrggrrr  
46      left  rrggrrr  
47  straight  rrggGGG

In [ ]:
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge_id)
        out_edge = self.net.getEdge(out_edge_id)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'inc_edge_id', 'out_edge_id', 'state']]


In [19]:
display(self.match6)
self.assign_signals() # 2-3 신호배정
display(self.match6)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

2-3. 직진 및 좌회전(G)을 배정했습니다.


inter_no node_id  phase_no ring_type  move_no    inc_edge_id  \
0         175      i0         1         A        8  -571542797_02   
1         175      i0         1         B        4  -571500487_01   
2         175      i0         2         A        7  -571500487_01   
3         175      i0         2         B        3  -571542797_02   
4         175      i0         3         A        6   571545870_02   
..        ...     ...       ...       ...      ...            ...   
103       210     u60         2         B        2            NaN   
104       210     u60         3         A        7            NaN   
105       210     u60         3         B        4            NaN   
106       210     u60         4         A        8            NaN   
107       210     u60         4         B        3            NaN   

      out_edge_id              state  
0    571500487_01  grrrgrrrgGGGGrgrr  
1    571542797_02  gGGrgrrrgrrrrrgrr  
2    571545870_01  grrGgrrrgrrrrrgrr  
3    571510153_01  grrrgrrrgrrrrGgrr  
4    571510153_01  grrrgGGrgrrrrrgrr  
..            ...                ...  
103           NaN          ggggggggr  
104           NaN          ggggggggr  
105           NaN          ggggggggr  
106           NaN          ggggggggr  
107           NaN          ggggggggr  

[108 rows x 8 columns]